In [1]:
!pip install pytorch-tabnet

In [2]:
import torch
from torch.nn import Linear, BatchNorm1d, ReLU
import numpy as np

from pytorch_tabnet import sparsemax

In [3]:
import pandas as pd
import numpy as np

In [4]:
# train_data = pd.read_csv("train\\train.csv")
# test_data = pd.read_csv("test\\test.csv")
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [5]:
train_data = pd.read_csv('/content/drive/My Drive/data.forest/train.csv')
test_data = pd.read_csv('/content/drive/My Drive/data.forest/test.csv')

In [6]:
X=train_data.drop(labels=['Id','Cover_Type'],axis=1)
y=train_data['Cover_Type']

In [7]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train,  y_test = train_test_split(X, y, test_size = 0.2, random_state=40)
y_test = y_test.to_numpy()
y_train = y_train.to_numpy()
X_train = X_train.to_numpy()
X_test = X_test.to_numpy()
for i, y in enumerate(y_train):
    y_train[i] = y_train[i] - 1
for i, y in enumerate(y_test):
    y_test[i] = y_test[i] - 1

In [8]:
def initialize_non_glu(module, input_dim, output_dim):
    gain_value = np.sqrt((input_dim + output_dim) / np.sqrt(4 * input_dim))
    torch.nn.init.xavier_normal_(module.weight, gain=gain_value)
    # torch.nn.init.zeros_(module.bias)
    return


def initialize_glu(module, input_dim, output_dim):
    gain_value = np.sqrt((input_dim + output_dim) / np.sqrt(input_dim))
    torch.nn.init.xavier_normal_(module.weight, gain=gain_value)
    # torch.nn.init.zeros_(module.bias)
    return

In [9]:
class GBN(torch.nn.Module):
    """
    Ghost Batch Normalization
    https://arxiv.org/abs/1705.08741
    """

    def __init__(self, input_dim, virtual_batch_size=128, momentum=0.01):
        super(GBN, self).__init__()

        self.input_dim = input_dim
        self.virtual_batch_size = virtual_batch_size
        self.bn = BatchNorm1d(self.input_dim, momentum=momentum)

    def forward(self, x):
        chunks = x.chunk(int(np.ceil(x.shape[0] / self.virtual_batch_size)), 0)
        res = [self.bn(x_) for x_ in chunks]

        return torch.cat(res, dim=0)

In [10]:
# gbn = GBN(54)
# gbn.forward(torch.FloatTensor(X_train[:5]))

In [11]:
class EmbeddingGenerator(torch.nn.Module):
    """
    Classical embeddings generator
    """

    def __init__(self, input_dim, cat_dims, cat_idxs, cat_emb_dim):
        """This is an embedding module for an entire set of features
        Parameters
        ----------
        input_dim : int
            Number of features coming as input (number of columns)
        cat_dims : list of int
            Number of modalities for each categorial features
            If the list is empty, no embeddings will be done
        cat_idxs : list of int
            Positional index for each categorical features in inputs
        cat_emb_dim : int or list of int
            Embedding dimension for each categorical features
            If int, the same embedding dimension will be used for all categorical features
        """
        super(EmbeddingGenerator, self).__init__()
        if cat_dims == [] and cat_idxs == []:
            self.skip_embedding = True
            self.post_embed_dim = input_dim
            return
        elif (cat_dims == []) ^ (cat_idxs == []):
            if cat_dims == []:
                msg = "If cat_idxs is non-empty, cat_dims must be defined as a list of same length."
            else:
                msg = "If cat_dims is non-empty, cat_idxs must be defined as a list of same length."
            raise ValueError(msg)
        elif len(cat_dims) != len(cat_idxs):
            msg = "The lists cat_dims and cat_idxs must have the same length."
            raise ValueError(msg)

        self.skip_embedding = False
        if isinstance(cat_emb_dim, int):
            self.cat_emb_dims = [cat_emb_dim] * len(cat_idxs)
        else:
            self.cat_emb_dims = cat_emb_dim

        # check that all embeddings are provided
        if len(self.cat_emb_dims) != len(cat_dims):
            msg = f"""cat_emb_dim and cat_dims must be lists of same length, got {len(self.cat_emb_dims)}
                      and {len(cat_dims)}"""
            raise ValueError(msg)
        self.post_embed_dim = int(
            input_dim + np.sum(self.cat_emb_dims) - len(self.cat_emb_dims)
        )

        self.embeddings = torch.nn.ModuleList()

        # Sort dims by cat_idx
        sorted_idxs = np.argsort(cat_idxs)
        cat_dims = [cat_dims[i] for i in sorted_idxs]
        self.cat_emb_dims = [self.cat_emb_dims[i] for i in sorted_idxs]

        for cat_dim, emb_dim in zip(cat_dims, self.cat_emb_dims):
            self.embeddings.append(torch.nn.Embedding(cat_dim, emb_dim))

        # record continuous indices
        self.continuous_idx = torch.ones(input_dim, dtype=torch.bool)
        self.continuous_idx[cat_idxs] = 0

    def forward(self, x):
        """
        Apply embeddings to inputs
        Inputs should be (batch_size, input_dim)
        Outputs will be of size (batch_size, self.post_embed_dim)
        """
        if self.skip_embedding:
            # no embeddings required
            return x

        cols = []
        cat_feat_counter = 0
        for feat_init_idx, is_continuous in enumerate(self.continuous_idx):
            # Enumerate through continuous idx boolean mask to apply embeddings
            if is_continuous:
                cols.append(x[:, feat_init_idx].float().view(-1, 1))
            else:
                cols.append(
                    self.embeddings[cat_feat_counter](x[:, feat_init_idx].long())
                )
                cat_feat_counter += 1
        # concat
        post_embeddings = torch.cat(cols, dim=1)
        return post_embeddings

In [12]:
class GLU_Layer(torch.nn.Module):
    def __init__(
        self, input_dim, output_dim, fc=None, virtual_batch_size=128, momentum=0.02
    ):
        super(GLU_Layer, self).__init__()

        self.output_dim = output_dim
        if fc:
            self.fc = fc
        else:
            self.fc = Linear(input_dim, 2 * output_dim, bias=False)
        initialize_glu(self.fc, input_dim, 2 * output_dim)

        self.bn = GBN(
            2 * output_dim, virtual_batch_size=virtual_batch_size, momentum=momentum
        )

    def forward(self, x):
        x = self.fc(x)
        x = self.bn(x)
        out = torch.mul(x[:, : self.output_dim], torch.sigmoid(x[:, self.output_dim :]))
        return out

In [13]:
# GLU = GLU_Layer(54, 1)

In [14]:
# GLU.forward(torch.FloatTensor(X_train[:5]))

In [15]:
class GLU_Block(torch.nn.Module):
    """
      Independent GLU block, specific to each step
    """

    def __init__(
        self,
        input_dim,
        output_dim,
        n_glu=2,
        first=False,
        shared_layers=None,
        virtual_batch_size=128,
        momentum=0.02,
    ):
        super().__init__()
        self.first = first
        self.shared_layers = shared_layers
        self.n_glu = n_glu
        self.glu_layers = torch.nn.ModuleList()

        params = {"virtual_batch_size": virtual_batch_size, "momentum": momentum}

        fc = shared_layers[0] if shared_layers else None
        self.glu_layers.append(GLU_Layer(input_dim, output_dim, fc=fc, **params))
        for glu_id in range(1, self.n_glu):
            fc = shared_layers[glu_id] if shared_layers else None
            self.glu_layers.append(GLU_Layer(output_dim, output_dim, fc=fc, **params))

    def forward(self, x):
        scale = torch.sqrt(torch.FloatTensor([0.5]).to(x.device))
        if self.first:  # the first layer of the block has no scale multiplication
            x = self.glu_layers[0](x)
            layers_left = range(1, self.n_glu)
        else:
            layers_left = range(self.n_glu)

        for glu_id in layers_left:
            x = torch.add(x, self.glu_layers[glu_id](x))
            x = x * scale
        return x

In [16]:
# glu_block = GLU_Block(54, 54)

In [17]:
# glu_block(torch.FloatTensor(X_train[:5]))

In [18]:
class FeatTransformer(torch.nn.Module):
    def __init__(
        self,
        input_dim,
        output_dim,
        shared_layers,
        n_glu_independent,
        virtual_batch_size=128,
        momentum=0.02,
    ):
        super().__init__()
        """
        Initialize a feature transformer.
        Parameters
        ----------
        input_dim : int
            Input size
        output_dim : int
            Output_size
        shared_layers : torch.nn.ModuleList
            The shared block that should be common to every step
        n_glu_independent : int
            Number of independent GLU layers
        virtual_batch_size : int
            Batch size for Ghost Batch Normalization within GLU block(s)
        momentum : float
            Float value between 0 and 1 which will be used for momentum in batch norm
        """

        params = {
            "n_glu": n_glu_independent,
            "virtual_batch_size": virtual_batch_size,
            "momentum": momentum,
        }

        if shared_layers is None:
            # no shared layers
            self.shared = torch.nn.Identity()
            is_first = True
        else:
            self.shared = GLU_Block(
                input_dim,
                output_dim,
                first=True,
                shared_layers=shared_layers,
                n_glu=len(shared_layers),
                virtual_batch_size=virtual_batch_size,
                momentum=momentum,
            )
            is_first = False

        if n_glu_independent == 0:
            # no independent layers
            self.specifics = torch.nn.Identity()
        else:
            spec_input_dim = input_dim if is_first else output_dim
            self.specifics = GLU_Block(
                spec_input_dim, output_dim, first=is_first, **params
            )

    def forward(self, x):
        x = self.shared(x)
        x = self.specifics(x)
        return x

In [19]:
# FT = FeatTransformer(54, 54, None, 2)

In [20]:
# FT.forward(torch.FloatTensor(X_train[:5]))

In [21]:
class AttentiveTransformer(torch.nn.Module):
    def __init__(
        self,
        input_dim,
        output_dim,
        virtual_batch_size=128,
        momentum=0.02,
        mask_type="sparsemax",
    ):
        """
        Initialize an attention transformer.
        Parameters
        ----------
        input_dim : int
            Input size
        output_dim : int
            Output_size
        virtual_batch_size : int
            Batch size for Ghost Batch Normalization
        momentum : float
            Float value between 0 and 1 which will be used for momentum in batch norm
        mask_type : str
            Either "sparsemax" or "entmax" : this is the masking function to use
        """
        super().__init__()
        self.fc = Linear(input_dim, output_dim, bias=False)
        initialize_non_glu(self.fc, input_dim, output_dim)
        self.bn = GBN(
            output_dim, virtual_batch_size=virtual_batch_size, momentum=momentum
        )

        if mask_type == "sparsemax":
            # Sparsemax
            self.selector = sparsemax.Sparsemax(dim=-1)
        elif mask_type == "entmax":
            # Entmax
            self.selector = sparsemax.Entmax15(dim=-1)
        else:
            raise NotImplementedError(
                "Please choose either sparsemax" + "or entmax as masktype"
            )

    def forward(self, priors, processed_feat):
        x = self.fc(processed_feat)
        x = self.bn(x)
        x = torch.mul(x, priors)
        x = self.selector(x)
        return x


In [22]:
# AtTr = AttentiveTransformer(54, 3)

In [23]:
class TabNetEncoder(torch.nn.Module):
    def __init__(
        self,
        input_dim,
        output_dim,
        n_d=8,
        n_a=8,
        n_steps=3,
        gamma=1.3,
        n_independent=2,
        n_shared=2,
        epsilon=1e-15,
        virtual_batch_size=128,
        momentum=0.02,
        mask_type="sparsemax",
    ):
        """
        Defines main part of the TabNet network without the embedding layers.
        Parameters
        ----------
        input_dim : int
            Number of features
        output_dim : int or list of int for multi task classification
            Dimension of network output
            examples : one for regression, 2 for binary classification etc...
        n_d : int
            Dimension of the prediction  layer (usually between 4 and 64)
        n_a : int
            Dimension of the attention  layer (usually between 4 and 64)
        n_steps : int
            Number of successive steps in the network (usually between 3 and 10)
        gamma : float
            Float above 1, scaling factor for attention updates (usually between 1.0 to 2.0)
        n_independent : int
            Number of independent GLU layer in each GLU block (default 2)
        n_shared : int
            Number of independent GLU layer in each GLU block (default 2)
        epsilon : float
            Avoid log(0), this should be kept very low
        virtual_batch_size : int
            Batch size for Ghost Batch Normalization
        momentum : float
            Float value between 0 and 1 which will be used for momentum in all batch norm
        mask_type : str
            Either "sparsemax" or "entmax" : this is the masking function to use
        """
        super().__init__()
        self.input_dim = input_dim
        self.output_dim = output_dim
        self.is_multi_task = isinstance(output_dim, list)
        self.n_d = n_d
        self.n_a = n_a
        self.n_steps = n_steps
        self.gamma = gamma
        self.epsilon = epsilon
        self.n_independent = n_independent
        self.n_shared = n_shared
        self.virtual_batch_size = virtual_batch_size
        self.mask_type = mask_type
        self.initial_bn = BatchNorm1d(self.input_dim, momentum=0.01)

        if self.n_shared > 0:
            shared_feat_transform = torch.nn.ModuleList()
            for i in range(self.n_shared):
                if i == 0:
                    shared_feat_transform.append(
                        Linear(self.input_dim, 2 * (n_d + n_a), bias=False)
                    )
                else:
                    shared_feat_transform.append(
                        Linear(n_d + n_a, 2 * (n_d + n_a), bias=False)
                    )

        else:
            shared_feat_transform = None

        self.initial_splitter = FeatTransformer(
            self.input_dim,
            n_d + n_a,
            shared_feat_transform,
            n_glu_independent=self.n_independent,
            virtual_batch_size=self.virtual_batch_size,
            momentum=momentum,
        )

        self.feat_transformers = torch.nn.ModuleList()
        self.att_transformers = torch.nn.ModuleList()

        for step in range(n_steps):
            transformer = FeatTransformer(
                self.input_dim,
                n_d + n_a,
                shared_feat_transform,
                n_glu_independent=self.n_independent,
                virtual_batch_size=self.virtual_batch_size,
                momentum=momentum,
            )
            attention = AttentiveTransformer(
                n_a,
                self.input_dim,
                virtual_batch_size=self.virtual_batch_size,
                momentum=momentum,
                mask_type=self.mask_type,
            )
            self.feat_transformers.append(transformer)
            self.att_transformers.append(attention)

    def forward(self, x, prior=None):
        x = self.initial_bn(x)

        if prior is None:
            prior = torch.ones(x.shape).to(x.device)

        M_loss = 0
        att = self.initial_splitter(x)[:, self.n_d :]

        steps_output = []
        for step in range(self.n_steps):
            M = self.att_transformers[step](prior, att)
            M_loss += torch.mean(
                torch.sum(torch.mul(M, torch.log(M + self.epsilon)), dim=1)
            )
            # update prior
            prior = torch.mul(self.gamma - M, prior)
            # output
            masked_x = torch.mul(M, x)
            out = self.feat_transformers[step](masked_x)
            d = ReLU()(out[:, : self.n_d])
            steps_output.append(d)
            # update attention
            att = out[:, self.n_d :]

        M_loss /= self.n_steps
        return steps_output, M_loss

    def forward_masks(self, x):
        x = self.initial_bn(x)

        prior = torch.ones(x.shape).to(x.device)
        M_explain = torch.zeros(x.shape).to(x.device)
        att = self.initial_splitter(x)[:, self.n_d :]
        masks = {}

        for step in range(self.n_steps):
            M = self.att_transformers[step](prior, att)
            masks[step] = M
            # update prior
            prior = torch.mul(self.gamma - M, prior)
            # output
            masked_x = torch.mul(M, x)
            out = self.feat_transformers[step](masked_x)
            d = ReLU()(out[:, : self.n_d])
            # explain
            step_importance = torch.sum(d, dim=1)
            M_explain += torch.mul(M, step_importance.unsqueeze(dim=1))
            # update attention
            att = out[:, self.n_d :]

        return M_explain, masks

In [24]:
tbencod = TabNetEncoder(54, 6)

In [25]:
tbencod.forward(torch.FloatTensor(X_train[:2]))

([tensor([[0.0000, 0.3414, 0.4604, 0.0000, 0.1883, 0.2987, 0.5121, 0.8818],
          [0.5047, 0.0000, 0.0000, 0.1451, 0.0000, 0.0000, 0.0345, 0.0000]],
         grad_fn=<ReluBackward0>),
  tensor([[0.5299, 0.0000, 0.8409, 0.0000, 0.2643, 0.8005, 0.0000, 0.0000],
          [0.0292, 0.0000, 0.0000, 0.0000, 0.0337, 0.0000, 0.0000, 0.5518]],
         grad_fn=<ReluBackward0>),
  tensor([[0.0000, 0.1442, 0.1410, 0.0760, 0.0329, 0.3364, 0.0000, 0.7457],
          [0.9408, 0.0000, 0.0000, 0.0000, 0.2115, 0.5463, 0.0354, 0.0000]],
         grad_fn=<ReluBackward0>)],
 tensor(-3.0967, grad_fn=<DivBackward0>))

In [26]:
class TabNetDecoder(torch.nn.Module):
    def __init__(
        self,
        input_dim,
        n_d=8,
        n_steps=3,
        n_independent=1,
        n_shared=1,
        virtual_batch_size=128,
        momentum=0.02,
    ):
        """
        Defines main part of the TabNet network without the embedding layers.
        Parameters
        ----------
        input_dim : int
            Number of features
        output_dim : int or list of int for multi task classification
            Dimension of network output
            examples : one for regression, 2 for binary classification etc...
        n_d : int
            Dimension of the prediction  layer (usually between 4 and 64)
        n_steps : int
            Number of successive steps in the network (usually between 3 and 10)
        gamma : float
            Float above 1, scaling factor for attention updates (usually between 1.0 to 2.0)
        n_independent : int
            Number of independent GLU layer in each GLU block (default 1)
        n_shared : int
            Number of independent GLU layer in each GLU block (default 1)
        virtual_batch_size : int
            Batch size for Ghost Batch Normalization
        momentum : float
            Float value between 0 and 1 which will be used for momentum in all batch norm
        """
        super().__init__()
        self.input_dim = input_dim
        self.n_d = n_d
        self.n_steps = n_steps
        self.n_independent = n_independent
        self.n_shared = n_shared
        self.virtual_batch_size = virtual_batch_size

        self.feat_transformers = torch.nn.ModuleList()

        if self.n_shared > 0:
            shared_feat_transform = torch.nn.ModuleList()
            for i in range(self.n_shared):
                if i == 0:
                    shared_feat_transform.append(Linear(n_d, 2 * n_d, bias=False))
                else:
                    shared_feat_transform.append(Linear(n_d, 2 * n_d, bias=False))

        else:
            shared_feat_transform = None

        for step in range(n_steps):
            transformer = FeatTransformer(
                n_d,
                n_d,
                shared_feat_transform,
                n_glu_independent=self.n_independent,
                virtual_batch_size=self.virtual_batch_size,
                momentum=momentum,
            )
            self.feat_transformers.append(transformer)

        self.reconstruction_layer = Linear(n_d, self.input_dim, bias=False)
        initialize_non_glu(self.reconstruction_layer, n_d, self.input_dim)

    def forward(self, steps_output):
        res = 0
        for step_nb, step_output in enumerate(steps_output):
            x = self.feat_transformers[step_nb](step_output)
            res = torch.add(res, x)
        res = self.reconstruction_layer(res)
        return res

In [27]:
tbdec = TabNetDecoder(54, 8)

In [28]:
tbencod.forward(torch.FloatTensor(X_train[:2]))[0][-1]

tensor([[0.0000, 0.1442, 0.1410, 0.0760, 0.0329, 0.3364, 0.0000, 0.7457],
        [0.9408, 0.0000, 0.0000, 0.0000, 0.2115, 0.5463, 0.0354, 0.0000]],
       grad_fn=<ReluBackward0>)

In [29]:
# class TabNetPretraining(torch.nn.Module):
#     def __init__(
#         self,
#         input_dim,
#         pretraining_ratio=0.2,
#         n_d=8,
#         n_a=8,
#         n_steps=3,
#         gamma=1.3,
#         cat_idxs=[],
#         cat_dims=[],
#         cat_emb_dim=1,
#         n_independent=2,
#         n_shared=2,
#         epsilon=1e-15,
#         virtual_batch_size=128,
#         momentum=0.02,
#         mask_type="sparsemax",
#         n_shared_decoder=1,
#         n_indep_decoder=1,
#     ):
#         super(TabNetPretraining, self).__init__()

#         self.cat_idxs = cat_idxs or []
#         self.cat_dims = cat_dims or []
#         self.cat_emb_dim = cat_emb_dim

#         self.input_dim = input_dim
#         self.n_d = n_d
#         self.n_a = n_a
#         self.n_steps = n_steps
#         self.gamma = gamma
#         self.epsilon = epsilon
#         self.n_independent = n_independent
#         self.n_shared = n_shared
#         self.mask_type = mask_type
#         self.pretraining_ratio = pretraining_ratio
#         self.n_shared_decoder = n_shared_decoder
#         self.n_indep_decoder = n_indep_decoder

#         if self.n_steps <= 0:
#             raise ValueError("n_steps should be a positive integer.")
#         if self.n_independent == 0 and self.n_shared == 0:
#             raise ValueError("n_shared and n_independent can't be both zero.")

#         self.virtual_batch_size = virtual_batch_size
#         self.embedder = EmbeddingGenerator(input_dim, cat_dims, cat_idxs, cat_emb_dim)
#         self.post_embed_dim = self.embedder.post_embed_dim

#         self.masker = RandomObfuscator(self.pretraining_ratio)
#         self.encoder = TabNetEncoder(
#             input_dim=self.post_embed_dim,
#             output_dim=self.post_embed_dim,
#             n_d=n_d,
#             n_a=n_a,
#             n_steps=n_steps,
#             gamma=gamma,
#             n_independent=n_independent,
#             n_shared=n_shared,
#             epsilon=epsilon,
#             virtual_batch_size=virtual_batch_size,
#             momentum=momentum,
#             mask_type=mask_type,
#         )
#         self.decoder = TabNetDecoder(
#             self.post_embed_dim,
#             n_d=n_d,
#             n_steps=n_steps,
#             n_independent=self.n_indep_decoder,
#             n_shared=self.n_shared_decoder,
#             virtual_batch_size=virtual_batch_size,
#             momentum=momentum,
#         )

#     def forward(self, x):
#         """
#         Returns: res, embedded_x, obf_vars
#             res : output of reconstruction
#             embedded_x : embedded input
#             obf_vars : which variable where obfuscated
#         """
#         embedded_x = self.embedder(x)
#         if self.training:
#             masked_x, obf_vars = self.masker(embedded_x)
#             # set prior of encoder with obf_mask
#             prior = 1 - obf_vars
#             steps_out, _ = self.encoder(masked_x, prior=prior)
#             res = self.decoder(steps_out)
#             return res, embedded_x, obf_vars
#         else:
#             steps_out, _ = self.encoder(embedded_x)
#             res = self.decoder(steps_out)
#             return res, embedded_x, torch.ones(embedded_x.shape).to(x.device)

#     def forward_masks(self, x):
#         embedded_x = self.embedder(x)
#         return self.encoder.forward_masks(embedded_x)

In [30]:
class TabNetNoEmbeddings(torch.nn.Module):
    def __init__(
        self,
        input_dim,
        output_dim,
        n_d=8,
        n_a=8,
        n_steps=3,
        gamma=1.3,
        n_independent=2,
        n_shared=2,
        epsilon=1e-15,
        virtual_batch_size=128,
        momentum=0.02,
        mask_type="sparsemax",
    ):
        """
        Defines main part of the TabNet network without the embedding layers.
        Parameters
        ----------
        input_dim : int
            Number of features
        output_dim : int or list of int for multi task classification
            Dimension of network output
            examples : one for regression, 2 for binary classification etc...
        n_d : int
            Dimension of the prediction  layer (usually between 4 and 64)
        n_a : int
            Dimension of the attention  layer (usually between 4 and 64)
        n_steps : int
            Number of successive steps in the network (usually between 3 and 10)
        gamma : float
            Float above 1, scaling factor for attention updates (usually between 1.0 to 2.0)
        n_independent : int
            Number of independent GLU layer in each GLU block (default 2)
        n_shared : int
            Number of independent GLU layer in each GLU block (default 2)
        epsilon : float
            Avoid log(0), this should be kept very low
        virtual_batch_size : int
            Batch size for Ghost Batch Normalization
        momentum : float
            Float value between 0 and 1 which will be used for momentum in all batch norm
        mask_type : str
            Either "sparsemax" or "entmax" : this is the masking function to use
        """
        super().__init__()
        self.input_dim = input_dim
        self.output_dim = output_dim
        self.is_multi_task = isinstance(output_dim, list)
        self.n_d = n_d
        self.n_a = n_a
        self.n_steps = n_steps
        self.gamma = gamma
        self.epsilon = epsilon
        self.n_independent = n_independent
        self.n_shared = n_shared
        self.virtual_batch_size = virtual_batch_size
        self.mask_type = mask_type
        self.initial_bn = BatchNorm1d(self.input_dim, momentum=0.01)

        self.encoder = TabNetEncoder(
            input_dim=input_dim,
            output_dim=output_dim,
            n_d=n_d,
            n_a=n_a,
            n_steps=n_steps,
            gamma=gamma,
            n_independent=n_independent,
            n_shared=n_shared,
            epsilon=epsilon,
            virtual_batch_size=virtual_batch_size,
            momentum=momentum,
            mask_type=mask_type,
        )

        if self.is_multi_task:
            self.multi_task_mappings = torch.nn.ModuleList()
            for task_dim in output_dim:
                task_mapping = Linear(n_d, task_dim, bias=False)
                initialize_non_glu(task_mapping, n_d, task_dim)
                self.multi_task_mappings.append(task_mapping)
        else:
            self.final_mapping = Linear(n_d, output_dim, bias=False)
            initialize_non_glu(self.final_mapping, n_d, output_dim)

    def forward(self, x):
        res = 0
        steps_output, M_loss = self.encoder(x)
        res = torch.sum(torch.stack(steps_output, dim=0), dim=0)

        if self.is_multi_task:
            # Result will be in list format
            out = []
            for task_mapping in self.multi_task_mappings:
                out.append(task_mapping(res))
        else:
            out = self.final_mapping(res)
        return out, M_loss

    def forward_masks(self, x):
        return self.encoder.forward_masks(x)

In [31]:
class TabNet(torch.nn.Module):
    def __init__(
        self,
        input_dim,
        output_dim,
        n_d=64,
        n_a=64,
        n_steps=5,
        gamma=1.3,
        cat_idxs=[],
        cat_dims=[],
        cat_emb_dim=1,
        n_independent=2,
        n_shared=2,
        epsilon=1e-15,
        virtual_batch_size=128,
        momentum=0.02,
        mask_type="sparsemax",
    ):
        """
        Defines TabNet network
        Parameters
        ----------
        input_dim : int
            Initial number of features
        output_dim : int
            Dimension of network output
            examples : one for regression, 2 for binary classification etc...
        n_d : int
            Dimension of the prediction  layer (usually between 4 and 64)
        n_a : int
            Dimension of the attention  layer (usually between 4 and 64)
        n_steps : int
            Number of successive steps in the network (usually between 3 and 10)
        gamma : float
            Float above 1, scaling factor for attention updates (usually between 1.0 to 2.0)
        cat_idxs : list of int
            Index of each categorical column in the dataset
        cat_dims : list of int
            Number of categories in each categorical column
        cat_emb_dim : int or list of int
            Size of the embedding of categorical features
            if int, all categorical features will have same embedding size
            if list of int, every corresponding feature will have specific size
        n_independent : int
            Number of independent GLU layer in each GLU block (default 2)
        n_shared : int
            Number of independent GLU layer in each GLU block (default 2)
        epsilon : float
            Avoid log(0), this should be kept very low
        virtual_batch_size : int
            Batch size for Ghost Batch Normalization
        momentum : float
            Float value between 0 and 1 which will be used for momentum in all batch norm
        mask_type : str
            Either "sparsemax" or "entmax" : this is the masking function to use
        """
        super().__init__()
        self.cat_idxs = cat_idxs or []
        self.cat_dims = cat_dims or []
        self.cat_emb_dim = cat_emb_dim

        self.input_dim = input_dim
        self.output_dim = output_dim
        self.n_d = n_d
        self.n_a = n_a
        self.n_steps = n_steps
        self.gamma = gamma
        self.epsilon = epsilon
        self.n_independent = n_independent
        self.n_shared = n_shared
        self.mask_type = mask_type

        if self.n_steps <= 0:
            raise ValueError("n_steps should be a positive integer.")
        if self.n_independent == 0 and self.n_shared == 0:
            raise ValueError("n_shared and n_independent can't be both zero.")

        self.virtual_batch_size = virtual_batch_size
        self.embedder = EmbeddingGenerator(input_dim, cat_dims, cat_idxs, cat_emb_dim)
        self.post_embed_dim = self.embedder.post_embed_dim
        self.tabnet = TabNetNoEmbeddings(
            self.post_embed_dim,
            output_dim,
            n_d,
            n_a,
            n_steps,
            gamma,
            n_independent,
            n_shared,
            epsilon,
            virtual_batch_size,
            momentum,
            mask_type,
        )

    def forward(self, x):
        x = self.embedder(x)
        return self.tabnet(x)

    def forward_masks(self, x):
        x = self.embedder(x)
        return self.tabnet.forward_masks(x)

In [34]:
e = TabNet(54, 7)
# F.cross_entropy(e[0], y_train[:5])
e.forward_masks(tens(X_train[:5]))

(tensor([[1.2594e+01, 0.0000e+00, 0.0000e+00, 0.0000e+00, 4.6928e+00, 2.0437e+00,
          0.0000e+00, 0.0000e+00, 0.0000e+00, 2.8934e+00, 0.0000e+00, 0.0000e+00,
          0.0000e+00, 0.0000e+00, 1.3656e+00, 3.4408e+00, 0.0000e+00, 0.0000e+00,
          1.1781e+00, 2.5317e+00, 2.8845e+00, 5.4579e-01, 0.0000e+00, 0.0000e+00,
          0.0000e+00, 0.0000e+00, 0.0000e+00, 5.4615e+00, 0.0000e+00, 1.1727e-01,
          0.0000e+00, 0.0000e+00, 0.0000e+00, 2.2954e+00, 0.0000e+00, 3.4280e+00,
          0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
          5.7685e+00, 4.1790e+00, 0.0000e+00, 1.2339e-02, 3.1996e+00, 1.6103e+00,
          1.3866e+00, 1.6021e+00, 0.0000e+00, 4.6944e+00, 0.0000e+00, 0.0000e+00],
         [3.1542e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 3.6881e+00,
          0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 1.4451e+00, 5.0934e+00,
          0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00, 0.0000e+00,
          0.000

In [35]:
from torch import FloatTensor as tens

In [36]:
from torch.utils.data import DataLoader

In [37]:
X_load = DataLoader(X_train, batch_size = 1000)
y_load = DataLoader(y_train, batch_size = 1000)

In [38]:
X_tens_train = torch.FloatTensor(X_train)
X_tens_test = torch.FloatTensor(X_test)

In [39]:
Train = []
Test = []
for i, x in enumerate(X_tens_train):
    Train.append((x, y_train[i]))
for i, x in enumerate(X_tens_test):
    Test.append((x, y_test[i]))
    

In [42]:
import os
from torch import nn, optim
from torch.nn import functional as F
from torch.utils.data import DataLoader
from catalyst import dl, metrics
# from catalyst.data import ToTensor
# from catalyst.contrib.datasets import MNIST

model = TabNet(54, 7)
optimizer = optim.Adam(model.parameters(), lr=0.02)

loaders = {
    "train": DataLoader(
        Train, batch_size=1000
    ),
    "valid": DataLoader(
        Test, batch_size=1000
    ),
}

class CustomRunner(dl.Runner):
    def predict_batch(self, batch):
        # model inference step
        return self.model(batch[0].to(self.device))

    def on_loader_start(self, runner):
        super().on_loader_start(runner)
        self.meters = {
            key: metrics.AdditiveValueMetric(compute_on_call=False)
            for key in ["loss", "accuracy01", "accuracy03"]
        }

    def handle_batch(self, batch):
        # model train/valid step
        # unpack the batch
        x, y = batch
        # run model forward pass
        logits, M_loss = self.model(x)
        # compute the loss
        loss = F.cross_entropy(logits, y)
        loss -= 0.001 * M_loss
        # compute the metrics
        accuracy01, accuracy03 = metrics.accuracy(logits, y, topk=(1, 3))
        # log metrics
        self.batch_metrics.update(
            {"loss": loss, "accuracy01": accuracy01, "accuracy03": accuracy03}
        )
        for key in ["loss", "accuracy01", "accuracy03"]:
            self.meters[key].update(self.batch_metrics[key].item(), self.batch_size)
        # run model backward pass
        if self.is_train_loader:
            loss.backward()
            self.optimizer.step()
            self.optimizer.zero_grad()

    def on_loader_end(self, runner):
        for key in ["loss", "accuracy01", "accuracy03"]:
            self.loader_metrics[key] = self.meters[key].compute()[0]
        super().on_loader_end(runner)

runner = CustomRunner()
# model training
runner.train(
    model=model,
    optimizer=optimizer,
    loaders=loaders,
    logdir="./logs",
    num_epochs=100,
    verbose=True,
    valid_loader="valid",
    valid_metric="loss",
    minimize_valid_metric=True,
)
# model inference
for logits in runner.predict_loader(loader=loaders["valid"]):
    assert logits.detach().cpu().numpy().shape[-1] == 7


train (1/100) accuracy01: 0.31704697304617163 | accuracy03: 0.6539352178849557 | loss: 2.174487790891103



valid (1/100) accuracy01: 0.15112434658739302 | accuracy03: 0.4907407559572704 | loss: 14.267767966739715
* Epoch (1/100) 



train (2/100) accuracy01: 0.4818121972222807 | accuracy03: 0.8769841652225566 | loss: 1.3244805507874364



valid (2/100) accuracy01: 0.14715609148578354 | accuracy03: 0.47619049400879593 | loss: 34.27926007023564
* Epoch (2/100) 



train (3/100) accuracy01: 0.5838293890473705 | accuracy03: 0.9521329902782643 | loss: 1.0427267740249004


...


train (99/100) accuracy01: 0.7423115341909348 | accuracy03: 0.9909887888601848 | loss: 0.612948936602426



valid (99/100) accuracy01: 0.71494712337615 | accuracy03: 0.9927248983156114 | loss: 0.7264400752133163
* Epoch (99/100) 



train (100/100) accuracy01: 0.7487599537880333 | accuracy03: 0.9909887987154501 | loss: 0.5860784664434731



valid (100/100) accuracy01: 0.7278439443578165 | accuracy03: 0.9914021679648647 | loss: 0.7024738895830024
* Epoch (100/100) 
Top best models:
logs/checkpoints/train.39.pth	0.6733


AttributeError: ignored

In [41]:
!pip install catalyst

     |████████████████████████████████| 536 kB 40.7 MB/s 
     |████████████████████████████████| 636 kB 53.1 MB/s 
     |████████████████████████████████| 120 kB 69.0 MB/s 
  Attempting uninstall: PyYAML
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13



train (1/1000) accuracy01: 0.8840939605992938 | accuracy03: 0.9993386574917368 | loss: 0.2867406399122306



valid (1/1000) accuracy01: 0.7232143349117703 | accuracy03: 0.9930555858309307 | loss: 0.8064489049255532
* Epoch (1/1000) 



train (2/1000) accuracy01: 0.8806217436594939 | accuracy03: 0.9994213283850403 | loss: 0.29520516014761394



valid (2/1000) accuracy01: 0.7162698773795334 | accuracy03: 0.992063531169185 | loss: 0.873454102605739
* Epoch (2/1000) 



train (3/1000) accuracy01: 0.8810350981260102 | accuracy03: 0.9995866701716468 | loss: 0.29381865978477495


...


valid (191/1000) accuracy01: 0.6726190919283206 | accuracy03: 0.9847884093012128 | loss: 0.9208845903003027
* Epoch (191/1000) 



train (192/1000) accuracy01: 0.7744709379064343 | accuracy03: 0.99446101565525 | loss: 0.5620902579809938



valid (192/1000) accuracy01: 0.683201093364645 | accuracy03: 0.9844577301431585 | loss: 0.8633098753671797
* Epoch (192/1000) 


Keyboard Interrupt



KeyboardInterrupt: ignored